In [3]:
from google.colab import drive
drive.mount('/content/drive')

Mounted at /content/drive


In [4]:
!unzip /content/drive/MyDrive/Dataset/archive.zip

Archive:  /content/drive/MyDrive/Dataset/archive.zip
  inflating: MICCAI_BraTS_2018_Data_Training/HGG/Brats18_2021_10_1/Brats18_2021_10_1_flair.nii  
  inflating: MICCAI_BraTS_2018_Data_Training/HGG/Brats18_2021_10_1/Brats18_2021_10_1_seg.nii  
  inflating: MICCAI_BraTS_2018_Data_Training/HGG/Brats18_2021_10_1/Brats18_2021_10_1_t1.nii  
  inflating: MICCAI_BraTS_2018_Data_Training/HGG/Brats18_2021_10_1/Brats18_2021_10_1_t1ce.nii  
  inflating: MICCAI_BraTS_2018_Data_Training/HGG/Brats18_2021_10_1/Brats18_2021_10_1_t2.nii  
  inflating: MICCAI_BraTS_2018_Data_Training/HGG/Brats18_2021_11_1/Brats18_2021_11_1_flair.nii  
  inflating: MICCAI_BraTS_2018_Data_Training/HGG/Brats18_2021_11_1/Brats18_2021_11_1_seg.nii  
  inflating: MICCAI_BraTS_2018_Data_Training/HGG/Brats18_2021_11_1/Brats18_2021_11_1_t1.nii  
  inflating: MICCAI_BraTS_2018_Data_Training/HGG/Brats18_2021_11_1/Brats18_2021_11_1_t1ce.nii  
  inflating: MICCAI_BraTS_2018_Data_Training/HGG/Brats18_2021_11_1/Brats18_2021_11_1_t2.n

## 3D-EDA on HGG

In [5]:
import nibabel as nib
import os
import albumentations as A
import numpy as np

class ImageReader:
    def __init__(
        self, root:str, img_size:int=256,
        normalize:bool=False, single_class:bool=False
    ) -> None:
        pad_size = 256 if img_size > 256 else 224
        self.resize = A.Compose(
            [
                A.PadIfNeeded(min_height=pad_size, min_width=pad_size, value=0),
                A.Resize(img_size, img_size)
            ]
        )
        self.normalize=normalize
        self.single_class=single_class
        self.root=root

    def read_file(self, path:str) -> dict:
        scan_type = path.split('_')[-1]
        raw_image = nib.load(path).get_fdata()
        raw_mask = nib.load(path.replace(scan_type, 'seg.nii')).get_fdata()
        processed_frames, processed_masks = [], []
        for frame_idx in range(raw_image.shape[2]):
            frame = raw_image[:, :, frame_idx]
            mask = raw_mask[:, :, frame_idx]
            resized = self.resize(image=frame, mask=mask)
            processed_frames.append(resized['image'])
            processed_masks.append(
                1*(resized['mask'] > 0) if self.single_class else resized['mask']
            )
        scan_data = np.stack(processed_frames, 0)
        if self.normalize:
            if scan_data.max() > 0:
                scan_data = scan_data/scan_data.max()
            scan_data = scan_data.astype(np.float32)
        return {
            'scan': scan_data,
            'segmentation': np.stack(processed_masks, 0),
            'orig_shape': raw_image.shape
        }

    def load_patient_scans(self, idx:int) -> dict:
        patient_id = str(idx).zfill(5)
        patient_dir = f'/content/MICCAI_BraTS_2018_Data_Training/HGG'
        scans = {}
        for folder_name in os.listdir(patient_dir):
            modality_dir = os.path.join(patient_dir, folder_name)
            if os.path.isdir(modality_dir):
                for file_name in os.listdir(modality_dir):
                    if file_name.endswith('.nii'):
                        scan_type = file_name.split('_')[-1].replace('.nii', '')
                        scan_filename = os.path.join(modality_dir, file_name)
                        scans[scan_type] = self.read_file(scan_filename)
        return scans


# Example usage
if __name__ == "__main__":
    # Example initialization
    root_dir = "/content/MICCAI_BraTS_2018_Data_Training"
    image_reader = ImageReader(root=root_dir, img_size=256, normalize=True, single_class=True)

    # Example loading scans for a patient
    patient_id = 1
    scans = image_reader.load_patient_scans(patient_id)
    print(scans.keys())  # Print the keys of the loaded scans


dict_keys(['seg', 't1ce', 't2', 't1', 'flair'])


In [6]:
import plotly.graph_objects as go
import numpy as np


def generate_3d_scatter(
    x:np.array, y:np.array, z:np.array, colors:np.array,
    size:int=3, opacity:float=0.2, scale:str='Teal',
    hover:str='skip', name:str='MRI'
) -> go.Scatter3d:
    return go.Scatter3d(
        x=x, y=y, z=z,
        mode='markers', hoverinfo=hover,
        marker = dict(
            size=size, opacity=opacity,
            color=colors, colorscale=scale
        ),
        name=name
    )


class ImageViewer3d():
    def __init__(
        self, reader:ImageReader,
        mri_downsample:int=10, mri_colorscale:str='Ice'
    ) -> None:
        self.reader = reader
        self.mri_downsample = mri_downsample
        self.mri_colorscale = mri_colorscale

    def load_clean_mri(self, image:np.array, orig_dim:int) -> dict:
        shape_offset = image.shape[1]/orig_dim
        z, x, y = (image > 0).nonzero()
        # only (1/mri_downsample) is sampled for the resulting image
        x, y, z = x[::self.mri_downsample], y[::self.mri_downsample], z[::self.mri_downsample]
        colors = image[z, x, y]
        return dict(x=x/shape_offset, y=y/shape_offset, z=z, colors=colors)

    def load_tumor_segmentation(self, image:np.array, orig_dim:int) -> dict:
        tumors = {}
        shape_offset = image.shape[1]/orig_dim
        # 1/1, 1/3 and 1/5 pixels for tumor tissue classes 1(core), 2(invaded) and 4(enhancing)
        sampling = {
            1: 1, 2: 3, 4: 5
        }
        for class_idx in sampling:
            z, x, y = (image == class_idx).nonzero()
            x, y, z = x[::sampling[class_idx]], y[::sampling[class_idx]], z[::sampling[class_idx]]
            tumors[class_idx] = dict(
                x=x/shape_offset, y=y/shape_offset, z=z,
                colors=class_idx/4
            )
        return tumors

    def collect_patient_data(self, scan:dict) -> tuple:
        clean_mri = self.load_clean_mri(scan['scan'], scan['orig_shape'][0])
        tumors = self.load_tumor_segmentation(scan['segmentation'], scan['orig_shape'][0])
        markers_created = clean_mri['x'].shape[0] + sum(tumors[class_idx]['x'].shape[0] for class_idx in tumors)
        return [
            generate_3d_scatter(
                **clean_mri, scale=self.mri_colorscale, opacity=0.4,
                hover='skip', name='Brain MRI'
            ),
            generate_3d_scatter(
                **tumors[1], opacity=0.8,
                hover='all', name='Necrotic tumor core'
            ),
            generate_3d_scatter(
                **tumors[2], opacity=0.4,
                hover='all', name='Peritumoral invaded tissue'
            ),
            generate_3d_scatter(
                **tumors[4], opacity=0.4,
                hover='all', name='GD-enhancing tumor'
            ),
        ], markers_created

    def get_3d_scan(self, patient_idx:int, scan_type:str='flair') -> go.Figure:
        scan = self.reader.load_patient_scans(patient_idx)[scan_type]
        data, num_markers = self.collect_patient_data(scan)
        fig = go.Figure(data=data)
        fig.update_layout(
            title=f"[Patient id:{patient_idx}] brain MRI scan ({num_markers} points)",
            legend_title="Pixel class (click to enable/disable)",
            font=dict(
                family="Courier New, monospace",
                size=14,
            ),
            margin=dict(
                l=0, r=0, b=0, t=30
            ),
            legend=dict(itemsizing='constant')
        )
        return fig

In [7]:
reader = ImageReader('./data', img_size=128, normalize=True, single_class=False)
viewer = ImageViewer3d(reader, mri_downsample=20)

In [8]:
!pip install plotly

In [9]:
import plotly.graph_objects as go
import numpy as np
import plotly.offline




In [10]:
fig = viewer.get_3d_scan(0, 't1')
plotly.offline.iplot(fig)

In [11]:
fig = viewer.get_3d_scan(9, 'flair')
plotly.offline.iplot(fig)

#3D-EDA on LGG

In [12]:
import nibabel as nib
import os
import albumentations as A
import numpy as np

class ImageReader:
    def __init__(
        self, root:str, img_size:int=256,
        normalize:bool=False, single_class:bool=False
    ) -> None:
        pad_size = 256 if img_size > 256 else 224
        self.resize = A.Compose(
            [
                A.PadIfNeeded(min_height=pad_size, min_width=pad_size, value=0),
                A.Resize(img_size, img_size)
            ]
        )
        self.normalize=normalize
        self.single_class=single_class
        self.root=root

    def read_file(self, path:str) -> dict:
        scan_type = path.split('_')[-1]
        raw_image = nib.load(path).get_fdata()
        raw_mask = nib.load(path.replace(scan_type, 'seg.nii')).get_fdata()
        processed_frames, processed_masks = [], []
        for frame_idx in range(raw_image.shape[2]):
            frame = raw_image[:, :, frame_idx]
            mask = raw_mask[:, :, frame_idx]
            resized = self.resize(image=frame, mask=mask)
            processed_frames.append(resized['image'])
            processed_masks.append(
                1*(resized['mask'] > 0) if self.single_class else resized['mask']
            )
        scan_data = np.stack(processed_frames, 0)
        if self.normalize:
            if scan_data.max() > 0:
                scan_data = scan_data/scan_data.max()
            scan_data = scan_data.astype(np.float32)
        return {
            'scan': scan_data,
            'segmentation': np.stack(processed_masks, 0),
            'orig_shape': raw_image.shape
        }

    def load_patient_scans(self, idx:int) -> dict:
        patient_id = str(idx).zfill(5)
        patient_dir = f'/content/MICCAI_BraTS_2018_Data_Training/LGG'
        scans = {}
        for folder_name in os.listdir(patient_dir):
            modality_dir = os.path.join(patient_dir, folder_name)
            if os.path.isdir(modality_dir):
                for file_name in os.listdir(modality_dir):
                    if file_name.endswith('.nii'):
                        scan_type = file_name.split('_')[-1].replace('.nii', '')
                        scan_filename = os.path.join(modality_dir, file_name)
                        scans[scan_type] = self.read_file(scan_filename)
        return scans


# Example usage
if __name__ == "__main__":
    # Example initialization
    root_dir = "/content/MICCAI_BraTS_2018_Data_Training"
    image_reader = ImageReader(root=root_dir, img_size=256, normalize=True, single_class=True)

    # Example loading scans for a patient
    patient_id = 1
    scans = image_reader.load_patient_scans(patient_id)
    print(scans.keys())  # Print the keys of the loaded scans


dict_keys(['flair', 't1ce', 't2', 't1', 'seg'])


In [13]:
import plotly.graph_objects as go
import numpy as np


def generate_3d_scatter(
    x:np.array, y:np.array, z:np.array, colors:np.array,
    size:int=3, opacity:float=0.2, scale:str='Teal',
    hover:str='skip', name:str='MRI'
) -> go.Scatter3d:
    return go.Scatter3d(
        x=x, y=y, z=z,
        mode='markers', hoverinfo=hover,
        marker = dict(
            size=size, opacity=opacity,
            color=colors, colorscale=scale
        ),
        name=name
    )


class ImageViewer3d():
    def __init__(
        self, reader:ImageReader,
        mri_downsample:int=10, mri_colorscale:str='Ice'
    ) -> None:
        self.reader = reader
        self.mri_downsample = mri_downsample
        self.mri_colorscale = mri_colorscale

    def load_clean_mri(self, image:np.array, orig_dim:int) -> dict:
        shape_offset = image.shape[1]/orig_dim
        z, x, y = (image > 0).nonzero()
        # only (1/mri_downsample) is sampled for the resulting image
        x, y, z = x[::self.mri_downsample], y[::self.mri_downsample], z[::self.mri_downsample]
        colors = image[z, x, y]
        return dict(x=x/shape_offset, y=y/shape_offset, z=z, colors=colors)

    def load_tumor_segmentation(self, image:np.array, orig_dim:int) -> dict:
        tumors = {}
        shape_offset = image.shape[1]/orig_dim
        # 1/1, 1/3 and 1/5 pixels for tumor tissue classes 1(core), 2(invaded) and 4(enhancing)
        sampling = {
            1: 1, 2: 3, 4: 5
        }
        for class_idx in sampling:
            z, x, y = (image == class_idx).nonzero()
            x, y, z = x[::sampling[class_idx]], y[::sampling[class_idx]], z[::sampling[class_idx]]
            tumors[class_idx] = dict(
                x=x/shape_offset, y=y/shape_offset, z=z,
                colors=class_idx/4
            )
        return tumors

    def collect_patient_data(self, scan:dict) -> tuple:
        clean_mri = self.load_clean_mri(scan['scan'], scan['orig_shape'][0])
        tumors = self.load_tumor_segmentation(scan['segmentation'], scan['orig_shape'][0])
        markers_created = clean_mri['x'].shape[0] + sum(tumors[class_idx]['x'].shape[0] for class_idx in tumors)
        return [
            generate_3d_scatter(
                **clean_mri, scale=self.mri_colorscale, opacity=0.4,
                hover='skip', name='Brain MRI'
            ),
            generate_3d_scatter(
                **tumors[1], opacity=0.8,
                hover='all', name='Necrotic tumor core'
            ),
            generate_3d_scatter(
                **tumors[2], opacity=0.4,
                hover='all', name='Peritumoral invaded tissue'
            ),
            generate_3d_scatter(
                **tumors[4], opacity=0.4,
                hover='all', name='GD-enhancing tumor'
            ),
        ], markers_created

    def get_3d_scan(self, patient_idx:int, scan_type:str='flair') -> go.Figure:
        scan = self.reader.load_patient_scans(patient_idx)[scan_type]
        data, num_markers = self.collect_patient_data(scan)
        fig = go.Figure(data=data)
        fig.update_layout(
            title=f"[Patient id:{patient_idx}] brain MRI scan ({num_markers} points)",
            legend_title="Pixel class (click to enable/disable)",
            font=dict(
                family="Courier New, monospace",
                size=14,
            ),
            margin=dict(
                l=0, r=0, b=0, t=30
            ),
            legend=dict(itemsizing='constant')
        )
        return fig

In [14]:
reader = ImageReader('./data', img_size=128, normalize=True, single_class=False)
viewer = ImageViewer3d(reader, mri_downsample=20)

In [15]:
fig = viewer.get_3d_scan(0, 't1')
plotly.offline.iplot(fig)

In [16]:
fig = viewer.get_3d_scan(9, 'flair')
plotly.offline.iplot(fig)

In [17]:
! pip install streamlit -q

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 8.1/8.1 MB 67.1 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 207.3/207.3 kB 26.9 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 7.0/7.0 MB 66.9 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 83.0/83.0 kB 11.8 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 62.7/62.7 kB 9.4 MB/s eta 0:00:00


In [18]:
pip install streamlit pandas plotly nibabel albumentations numpy

In [39]:
!wget -q -O - ipv4.icanhazip.com

34.126.147.135


In [ ]:
!streamlit run 'streamlit.py' --server.port=8502 & npx localtunnel --port 8502




  You can now view your Streamlit app in your browser.

  Network URL: http://172.28.0.12:8502
  External URL: http://34.126.147.135:8502

npx: installed 22 in 1.379s
your url is: https://tricky-turkeys-sell.loca.lt


In [20]:
import streamlit as st
import pandas as pd
import plotly.graph_objects as go
import numpy as np
import nibabel as nib
import albumentations as A


In [21]:
import streamlit as st
import pandas as pd
import plotly.graph_objects as go
import numpy as np
import nibabel as nib
import albumentations as A

# Import classes from the EDA code
class ImageReader:
    def __init__(
        self, root:str, img_size:int=256,
        normalize:bool=False, single_class:bool=False
    ) -> None:
        pad_size = 256 if img_size > 256 else 224
        self.resize = A.Compose(
            [
                A.PadIfNeeded(min_height=pad_size, min_width=pad_size, value=0),
                A.Resize(img_size, img_size)
            ]
        )
        self.normalize = normalize
        self.single_class = single_class
        self.root = root

    def read_file(self, path:str) -> dict:
        scan_type = path.split('_')[-1]
        raw_image = nib.load(path).get_fdata()
        raw_mask = nib.load(path.replace(scan_type, 'seg.nii')).get_fdata()
        processed_frames, processed_masks = [], []
        for frame_idx in range(raw_image.shape[2]):
            frame = raw_image[:, :, frame_idx]
            mask = raw_mask[:, :, frame_idx]
            resized = self.resize(image=frame, mask=mask)
            processed_frames.append(resized['image'])
            processed_masks.append(
                1 * (resized['mask'] > 0) if self.single_class else resized['mask']
            )
        scan_data = np.stack(processed_frames, 0)
        if self.normalize:
            if scan_data.max() > 0:
                scan_data = scan_data / scan_data.max()
            scan_data = scan_data.astype(np.float32)
        return {
            'scan': scan_data,
            'segmentation': np.stack(processed_masks, 0),
            'orig_shape': raw_image.shape
        }

    def load_patient_scans(self, idx:int) -> dict:
        patient_id = str(idx).zfill(5)
        patient_dir = f'/content/MICCAI_BraTS_2018_Data_Training/HGG'
        scans = {}
        for folder_name in os.listdir(patient_dir):
            modality_dir = os.path.join(patient_dir, folder_name)
            if os.path.isdir(modality_dir):
                for file_name in os.listdir(modality_dir):
                    if file_name.endswith('.nii'):
                        scan_type = file_name.split('_')[-1].replace('.nii', '')
                        scan_filename = os.path.join(modality_dir, file_name)
                        scans[scan_type] = self.read_file(scan_filename)
        return scans

class ImageViewer3d:
    def __init__(
        self, reader:ImageReader,
        mri_downsample:int=10, mri_colorscale:str='Ice'
    ) -> None:
        self.reader = reader
        self.mri_downsample = mri_downsample
        self.mri_colorscale = mri_colorscale

    def load_clean_mri(self, image:np.array, orig_dim:int) -> dict:
        shape_offset = image.shape[1] / orig_dim
        z, x, y = (image > 0).nonzero()
        x, y, z = x[::self.mri_downsample], y[::self.mri_downsample], z[::self.mri_downsample]
        colors = image[z, x, y]
        return dict(x=x / shape_offset, y=y / shape_offset, z=z, colors=colors)

    def load_tumor_segmentation(self, image:np.array, orig_dim:int) -> dict:
        tumors = {}
        shape_offset = image.shape[1] / orig_dim
        sampling = {
            1: 1, 2: 3, 4: 5
        }
        for class_idx in sampling:
            z, x, y = (image == class_idx).nonzero()
            x, y, z = x[::sampling[class_idx]], y[::sampling[class_idx]], z[::sampling[class_idx]]
            tumors[class_idx] = dict(
                x=x / shape_offset, y=y / shape_offset, z=z,
                colors=class_idx / 4
            )
        return tumors

    def collect_patient_data(self, scan:dict) -> tuple:
        clean_mri = self.load_clean_mri(scan['scan'], scan['orig_shape'][0])
        tumors = self.load_tumor_segmentation(scan['segmentation'], scan['orig_shape'][0])
        markers_created = clean_mri['x'].shape[0] + sum(
            tumors[class_idx]['x'].shape[0] for class_idx in tumors
        )
        return [
            generate_3d_scatter(
                **clean_mri, scale=self.mri_colorscale, opacity=0.4,
                hover='skip', name='Brain MRI'
            ),
            generate_3d_scatter(
                **tumors[1], opacity=0.8,
                hover='all', name='Necrotic tumor core'
            ),
            generate_3d_scatter(
                **tumors[2], opacity=0.4,
                hover='all', name='Peritumoral invaded tissue'
            ),
            generate_3d_scatter(
                **tumors[4], opacity=0.4,
                hover='all', name='GD-enhancing tumor'
            ),
        ], markers_created

    def get_3d_scan(self, patient_idx:int, scan_type:str='flair') -> go.Figure:
        scan = self.reader.load_patient_scans(patient_idx)[scan_type]
        data, num_markers = self.collect_patient_data(scan)
        fig = go.Figure(data=data)
        fig.update_layout(
            title=f"[Patient id:{patient_idx}] brain MRI scan ({num_markers} points)",
            legend_title="Pixel class (click to enable/disable)",
            font=dict(
                family="Courier New, monospace",
                size=14,
            ),
            margin=dict(
                l=0, r=0, b=0, t=30
            ),
            legend=dict(itemsizing='constant')
        )
        return fig

# Helper function for generating a 3D scatter plot
def generate_3d_scatter(
    x: np.array, y: np.array, z: np.array, colors: np.array,
    size: int = 3, opacity: float = 0.2, scale: str = 'Teal',
    hover: str = 'skip', name: str = 'MRI'
) -> go.Scatter3d:
    return go.Scatter3d(
        x=x, y=y, z=z,
        mode='markers', hoverinfo=hover,
        marker=dict(
            size=size, opacity=opacity,
            color=colors, colorscale=scale
        ),
        name=name
    )

def main():
    st.title("Brain MRI 3D-EDA Visualization App")
    st.write("Input the patient ID to view their specific brain MRI scan.")

    # Get user input for patient_id and scan_type
    patient_id = st.number_input("Enter the patient ID:", min_value=0, step=1, value=0)
    scan_type = st.selectbox("Select the scan type:", options=["flair", "t1", "t2", "t1ce"])

    # Initialize ImageReader and ImageViewer3d
    root_dir = "/content/MICCAI_BraTS_2018_Data_Training"
    image_reader = ImageReader(root=root_dir, img_size=256, normalize=True, single_class=True)
    viewer = ImageViewer3d(image_reader, mri_downsample=10)

    # Get 3D scan based on user input
    if st.button("Display MRI Scan"):
        fig = viewer.get_3d_scan(patient_id, scan_type)
        st.plotly_chart(fig)

if __name__ == "__main__":
    main()


2024-04-24 19:18:22.411 
  command:

    streamlit run /usr/local/lib/python3.10/dist-packages/colab_kernel_launcher.py [ARGUMENTS]


In [24]:
!streamlit run /usr/local/lib/python3.10/dist-packages/colab_kernel_launcher.py & npx localtunnel --port 8501




  You can now view your Streamlit app in your browser.

  Network URL: http://172.28.0.12:8501
  External URL: http://34.126.147.135:8501

npx: installed 22 in 3.208s
your url is: https://tough-hairs-wish.loca.lt
[ColabKernelApp] ERROR | Unable to initialize signal:
Traceback (most recent call last):
  File "/usr/local/lib/python3.10/dist-packages/ipykernel/kernelapp.py", line 583, in initialize
    self.init_signal()
  File "/usr/local/lib/python3.10/dist-packages/ipykernel/kernelapp.py", line 435, in init_signal
    signal.signal(signal.SIGINT, signal.SIG_IGN)
  File "/usr/lib/python3.10/signal.py", line 56, in signal
    handler = _signal.signal(_enum_to_int(signalnum), _enum_to_int(handler))
ValueError: signal only works in main thread of the main interpreter
[ColabKernelApp] WARNING | Parent appears to have exited, shutting down.
^C


In [26]:
pip install pyngrok


In [27]:
from pyngrok import ngrok

# Create a tunnel on port 8501
public_url = ngrok.connect(port=8501)
print("Streamlit app running at:", public_url)


ERROR:pyngrok.process.ngrok:t=2024-04-24T19:38:12+0000 lvl=eror msg="failed to reconnect session" obj=tunnels.session err="authentication failed: Usage of ngrok requires a verified account and authtoken.\n\nSign up for an account: https://dashboard.ngrok.com/signup\nInstall your authtoken: https://dashboard.ngrok.com/get-started/your-authtoken\r\n\r\nERR_NGROK_4018\r\n"
ERROR:pyngrok.process.ngrok:t=2024-04-24T19:38:12+0000 lvl=eror msg="session closing" obj=tunnels.session err="authentication failed: Usage of ngrok requires a verified account and authtoken.\n\nSign up for an account: https://dashboard.ngrok.com/signup\nInstall your authtoken: https://dashboard.ngrok.com/get-started/your-authtoken\r\n\r\nERR_NGROK_4018\r\n"
ERROR:pyngrok.process.ngrok:t=2024-04-24T19:38:12+0000 lvl=eror msg="terminating with error" obj=app err="authentication failed: Usage of ngrok requires a verified account and authtoken.\n\nSign up for an account: https://dashboard.ngrok.com/signup\nInstall your aut

PyngrokNgrokError: The ngrok process errored on start: authentication failed: Usage of ngrok requires a verified account and authtoken.\n\nSign up for an account: https://dashboard.ngrok.com/signup\nInstall your authtoken: https://dashboard.ngrok.com/get-started/your-authtoken\r\n\r\nERR_NGROK_4018\r\n.

In [34]:
!ngrok authtoken

authtoken - 

USAGE:
  ngrok authtoken TOKEN [flags]

AUTHOR:
  ngrok - <support@ngrok.com>

COMMANDS: 
  config          update or migrate ngrok's configuration file
  http            start an HTTP tunnel
  tcp             start a TCP tunnel
  tunnel          start a tunnel for use with a tunnel-group backend

EXAMPLES: 
  ngrok http 80                                                 # secure public URL for port 80 web server
  ngrok http --domain baz.ngrok.dev 8080                        # port 8080 available at baz.ngrok.dev
  ngrok tcp 22                                                  # tunnel arbitrary TCP traffic to port 22
  ngrok http 80 --oauth=google --oauth-allow-email=foo@foo.com  # secure your app with oauth

Paid Features: 
  ngrok http 80 --domain mydomain.com                           # run ngrok with your own custom domain
  ngrok http 80 --allow-cidr 2600:8c00::a03c:91ee:fe69:9695/32  # run ngrok with IP policy restrictions
  Upgrade your account at https://dashboar

In [29]:
!ngrok config add-authtoken YOUR_AUTH_TOKEN

Authtoken saved to configuration file: /root/.config/ngrok/ngrok.yml


In [31]:
!export NGROK_AUTH_TOKEN=$authtoken



In [36]:
from pyngrok import ngrok

# Create a tunnel on port 8501
public_url = ngrok.connect(port=8501)
print("Streamlit app running at:", public_url)


ERROR:pyngrok.process.ngrok:t=2024-04-24T19:44:07+0000 lvl=eror msg="failed to reconnect session" obj=tunnels.session err="authentication failed: The authtoken you specified does not look like a proper ngrok tunnel authtoken.\nYour authtoken: YOUR_AUTH_TOKEN\nInstructions to install your authtoken are on your ngrok dashboard:\nhttps://dashboard.ngrok.com/get-started/your-authtoken\r\n\r\nERR_NGROK_105\r\n"
ERROR:pyngrok.process.ngrok:t=2024-04-24T19:44:07+0000 lvl=eror msg="session closing" obj=tunnels.session err="authentication failed: The authtoken you specified does not look like a proper ngrok tunnel authtoken.\nYour authtoken: YOUR_AUTH_TOKEN\nInstructions to install your authtoken are on your ngrok dashboard:\nhttps://dashboard.ngrok.com/get-started/your-authtoken\r\n\r\nERR_NGROK_105\r\n"


PyngrokNgrokError: The ngrok process errored on start: authentication failed: The authtoken you specified does not look like a proper ngrok tunnel authtoken.\nYour authtoken: YOUR_AUTH_TOKEN\nInstructions to install your authtoken are on your ngrok dashboard:\nhttps://dashboard.ngrok.com/get-started/your-authtoken\r\n\r\nERR_NGROK_105\r\n.

In [ ]:
python streamlit.py


In [ ]:
streamlit run streamlit.py
